In [1]:
import numpy as np
import pandas as pd
import geopandas as gpd
import folium
import datetime
import pickle
from shapely.geometry import Point

In [2]:
promise_zone = gpd.read_file('../data/MDHA_Promise_Zones/Export_Output_5.shp')
print(promise_zone.crs)
promise_zone.head(7 )

epsg:2274


OBJECTID  ZONE_ID    SHAPE_STAr     SHAPE_STLe  \
0         1        1  1.053728e+08   49364.601403   
1         2        2  7.670585e+07   45226.018917   
2         3        3  2.985488e+08   75207.067487   
3         4        4  2.713638e+08   74348.596054   
4         5        5  3.928178e+08  106661.712102   
5         6        6  9.535996e+07   59256.923574   

                                            geometry  
0  POLYGON ((1743366.812 678044.543, 1743367.698 ...  
1  POLYGON ((1738690.545 661791.347, 1738733.644 ...  
2  POLYGON ((1759602.544 668309.889, 1759640.155 ...  
3  POLYGON ((1747799.003 654974.612, 1747821.293 ...  
4  POLYGON ((1737013.744 692634.639, 1737122.605 ...  
5  POLYGON ((1716935.654 667534.495, 1716992.481 ...

In [3]:
promise_zone = promise_zone.to_crs(epsg = 4326)

In [4]:
polygon_zone_5 = promise_zone.loc[promise_zone['ZONE_ID']==5]
polygon_zone_5.head()

OBJECTID  ZONE_ID    SHAPE_STAr     SHAPE_STLe  \
4         5        5  3.928178e+08  106661.712102   

                                            geometry  
4  POLYGON ((-86.78490 36.23358, -86.78452 36.232...

In [5]:
bus_stops = pd.read_csv('../data/busstops_cleaned.csv')
print(bus_stops.shape)
bus_stops.head(3)

(2524, 5)


stop              route  \
0  GREEN LN & WHITES CREEK PIKE WB      GOLDEN VALLEY   
1    _ 9TH AVE S & EDGEHILL AVE SB   8TH AVENUE SOUTH   
2   DONELSON/DELL STATION OUTBOUND  MURFREESBORO PIKE   

                  location        lat        lng  
0  (36.236249, -86.816722)  36.236249 -86.816722  
1  (36.142642, -86.780897)  36.142642 -86.780897  
2  (36.105615, -86.672004)  36.105615 -86.672004

In [6]:
bus_stops['geometry'] = bus_stops.apply(lambda x: Point((x.lng,x.lat)),
                                        axis=1)
bus_stops.head(3)

stop              route  \
0  GREEN LN & WHITES CREEK PIKE WB      GOLDEN VALLEY   
1    _ 9TH AVE S & EDGEHILL AVE SB   8TH AVENUE SOUTH   
2   DONELSON/DELL STATION OUTBOUND  MURFREESBORO PIKE   

                  location        lat        lng                      geometry  
0  (36.236249, -86.816722)  36.236249 -86.816722  POINT (-86.816722 36.236249)  
1  (36.142642, -86.780897)  36.142642 -86.780897  POINT (-86.780897 36.142642)  
2  (36.105615, -86.672004)  36.105615 -86.672004  POINT (-86.672004 36.105615)

In [7]:
bus_geo = gpd.GeoDataFrame(bus_stops, 
                           crs = promise_zone.crs, 
                           geometry = bus_stops['geometry'])

In [8]:
stops_by_zone = gpd.sjoin( bus_geo,polygon_zone_5, op = 'within')

C:\Users\RMAUR\anaconda3\envs\geo_env\lib\site-packages\IPython\core\interactiveshell.py:3364: FutureWarning: The `op` parameter is deprecated and will be removed in a future release. Please use the `predicate` parameter instead.
  if (await self.run_code(code, result,  async_=asy)):


In [9]:
zone_5_center = polygon_zone_5.centroid

C:\Users\RMAUR\AppData\Local\Temp/ipykernel_5592/806582915.py:1: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  zone_5_center = polygon_zone_5.centroid


In [10]:
stops_in_zone5 = stops_by_zone.loc[stops_by_zone['ZONE_ID']==5]

In [11]:
zone_5_area = (zone_5_center.y,zone_5_center.x)

In [12]:
map_area_5 = folium.Map(location =  zone_5_area, zoom_start = 12)

folium.GeoJson(polygon_zone_5).add_to(map_area_5)

for row_index, row_values in stops_in_zone5.iterrows():
    loc = [row_values['lat'], row_values['lng']]
    pop = str(row_values['route'])
    icon=folium.Icon(color="blue",icon="bus", prefix='fa')
    
    marker = folium.Marker(
        location = loc, 
        popup = pop, icon = icon) 

    marker.add_to(map_area_5)

map_area_5

In [12]:
# Import the file as a Pandas DataFrame
fp = '../data/july.csv'
july = pd.read_csv(fp)

In [13]:
company_dict = {'Bird':0, 'Lyft': 1, 'Gotcha': 2, 'Lime': 3, 'Spin': 4, 'Jump': 5, 'Bolt': 6}
july.companyname = july.companyname.replace(company_dict)

In [14]:
july.pubdatetime = pd.to_datetime(july['pubdatetime'])

In [15]:
july.to_pickle("../data/july.pkl")

In [16]:
july_scooters = july[['pubdatetime', 'latitude', 'longitude', 'sumdid', 'chargelevel', 'companyname']]

In [17]:
july_1_scooters = july_scooters[july_scooters['pubdatetime']<='2019-07-02 00:00:00.000'] 

In [18]:
july_6_scooters = july_scooters[july_scooters['pubdatetime'].between('2019-07-06 00:00:00.000','2019-07-07 00:00:00.000')] b

SyntaxError: invalid syntax (Temp/ipykernel_5592/2168254975.py, line 1)

In [ ]:
july_6_scooters =  july_6_scooters.set_index('pubdatetime')

In [19]:
july_1_scooters = july_1_scooters.set_index('pubdatetime')

In [20]:
july_1_scooters['geometry'] = july_1_scooters.apply(lambda x: Point(float(x.longitude), float(x.latitude)),axis=1)

In [21]:
july_1_scooters.head()

latitude  longitude         sumdid  chargelevel  \
pubdatetime                                                                 
2019-07-01 00:00:33.550  36.156678 -86.809004  Powered635135         22.0   
2019-07-01 00:00:34.973  36.145674 -86.794138  Powered790946         33.0   
2019-07-01 00:00:41.183  36.179319 -86.751538  Powered570380         76.0   
2019-07-01 00:00:41.620  36.152111 -86.803821  Powered240631         43.0   
2019-07-01 00:00:45.087  36.149355 -86.797550  Powered970404         52.0   

                         companyname                      geometry  
pubdatetime                                                         
2019-07-01 00:00:33.550            1  POINT (-86.809004 36.156678)  
2019-07-01 00:00:34.973            1  POINT (-86.794138 36.145674)  
2019-07-01 00:00:41.183            1  POINT (-86.751538 36.179319)  
2019-07-01 00:00:41.620            1  POINT (-86.803821 36.152111)  
2019-07-01 00:00:45.087            1   POINT (-86.79755 36.149355)

In [37]:
july_6_scooters['geometry'] = july_6_scooters.apply(lambda x: Point(float(x.longitude), float(x.latitude)),axis=1)

In [21]:
scoots_geo = gpd.GeoDataFrame(july_1_scooters,crs=promise_zone.crs,geometry=july_1_scooters.geometry)

In [38]:
jul6_scoots_geo = gpd.GeoDataFrame(july_6_scooters,crs=promise_zone.crs,geometry=july_6_scooters.geometry)

In [39]:
jul6_scoots_by_zone = gpd.sjoin( jul6_scoots_geo,promise_zone, op = 'within')

C:\Users\RMAUR\anaconda3\envs\geo_env\lib\site-packages\IPython\core\interactiveshell.py:3364: FutureWarning: The `op` parameter is deprecated and will be removed in a future release. Please use the `predicate` parameter instead.
  if (await self.run_code(code, result,  async_=asy)):


In [23]:
jul1_scoots_zone5 = scoots_by_zone.loc[scoots_by_zone['ZONE_ID']==5]

In [24]:
type(jul1_scoots_zone5.index)

pandas.core.indexes.datetimes.DatetimeIndex

In [25]:
# Create an empty list
df_hour_list = []

# Create a series with the different hours of the day
hours = pd.Series(jul1_scoots_zone5.index.hour.unique().sort_values())

# Create a list of points for each hour of the day
def create_list(hour):
    df_hour_list.append(jul1_scoots_zone5.loc[jul1_scoots_zone5.index.hour == hour,
                                ['latitude',
                                 'longitude']].
                        groupby(['latitude', 
                                 'longitude']).sum().reset_index().values.tolist())
hours.apply(create_list);

In [26]:
from folium.plugins import HeatMapWithTime
from folium.plugins import DualMap

# Add trip events to the map
zone5_map_time = folium.Map(location = zone_5_area, 
                      tiles="CartoDB Positron", 
                      zoom_start=13)


folium.GeoJson(polygon_zone_5).add_to(zone5_map_time)


HeatMapWithTime(df_hour_list, 
                auto_play=False, 
                max_opacity=0.5, 
                gradient = {0.2: '#FBD973', 
                            0.4: '#fa782f', 
                            0.75: '#F16578', 
                            1: '#782890'}).add_to(zone5_map_time)
zone5_map_time.save('../maps/zone5_map_time.html')
zone5_map_time

In [42]:
# Create an empty list
jul6_hour_list = []

# Create a series with the different hours of the day
jul6_hours = pd.Series(jul6_scoots_by_zone.index.hour.unique().sort_values())

# Create a list of points for each hour of the day
def create_list(hour):
    jul6_hour_list.append(jul6_scoots_by_zone.loc[jul6_scoots_by_zone.index.hour == hour,
                                ['latitude',
                                 'longitude']].
                        groupby(['latitude', 
                                 'longitude']).sum().reset_index().values.tolist())
hours.apply(create_list);

In [43]:
from folium.plugins import HeatMapWithTime

# Add trip events to the map
jul6_map_time = folium.Map(location = zone_5_area, 
                      tiles="CartoDB Positron", 
                      zoom_start=12)


folium.GeoJson(promise_zone).add_to(jul6_map_time)


HeatMapWithTime(jul6_hour_list, 
                auto_play=False, 
                max_opacity=0.5, 
                gradient = {0.2: '#FBD973', 
                            0.4: '#fa782f', 
                            0.75: '#F16578', 
                            1: '#782890'}).add_to(jul6_map_time)
jul6_map_time.save('../maps/zone5_map_time.html')
jul6_map_time